<a href="https://colab.research.google.com/github/shiki-fujin/DS-MLE-exam/blob/main/text_classification_sst2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Initializations

In [2]:
!apt install git-lfs

Reading package lists... Done
Building dependency tree       
Reading state information... Done
git-lfs is already the newest version (2.9.2-1).
0 upgraded, 0 newly installed, 0 to remove and 23 not upgraded.


In [3]:
! pip install datasets transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 452.9/452.9 KB 9.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.8/5.8 MB 62.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 182.4/182.4 KB 17.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 213.0/213.0 KB 17.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 132.0/132.0 KB 12.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 52.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 140.6/140.6 KB 13.4 MB/s eta 0:00:00
  Attempting uninstall: urllib3
    Found existing installation: urllib3 1.24.3
    Uninstalling urllib3-1.24.3:
      Successfully uninstalled urllib3-1.24.3


In [4]:
! pip install evaluate

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.4/81.4 KB 3.2 MB/s eta 0:00:00


In [5]:
! pip install ray[tune]

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.4/57.4 MB 9.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.8/8.8 MB 75.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 125.4/125.4 KB 12.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 468.5/468.5 KB 30.7 MB/s eta 0:00:00


In [6]:
import random
import pandas as pd
import numpy as np

In [7]:
from huggingface_hub import notebook_login
import transformers
import datasets
import evaluate
from ray import tune

In [8]:
notebook_login()

Token is valid.
Your token has been saved in your configured git credential helpers (store).
Your token has been saved to /root/.huggingface/token
Login successful


## Fine-tuning another dataset provided : **SST-2** (*sentiment analysis*)


In [10]:
# seed for reproducibility
random_seed = 30

### Prepare dataset

In [11]:
def encode_sst2(examples):
    return tokenizer(examples['sentence'], truncation=True)


def load_data(task):
  dataset = datasets.load_dataset('glue', task)
  metric = evaluate.load('glue', task)
  
  encoded_dataset = dataset.map(encode_sst2, batched=True)
  train_dataset = encoded_dataset['train'].shuffle(seed=random_seed).select(range(850))
  eval_dataset = encoded_dataset['validation'].shuffle(seed=random_seed).select(range(850))
  return train_dataset, eval_dataset, metric


actual_task = 'sst2'
pretrained_model_name = 'distilbert-base-uncased'
tokenizer = transformers.AutoTokenizer.from_pretrained(pretrained_model_name, use_fast=True)
train_dataset, eval_dataset, metric = load_data(actual_task)

  0%|          | 0/3 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?ba/s]

### Fine tuning using default args

In [12]:
def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return metric.compute(predictions=predictions, references=labels)

def model_init():
    return transformers.AutoModelForSequenceClassification.from_pretrained(pretrained_model_name, num_labels=2)


# trigger downloading and caching
transformers.AutoModelForSequenceClassification.from_pretrained(pretrained_model_name, num_labels=2)

Downloading:   0%|          | 0.00/268M [00:00<?, ?B/s]

Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.bias', 'vocab_transform.weight', 'vocab_layer_norm.weight', 'vocab_projector.bias', 'vocab_layer_norm.bias', 'vocab_projector.weight']
- This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['classifier.bias', 'pre_classifier.weight', 'pre_classi

DistilBertForSequenceClassification(
  (distilbert): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0): TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)
       

In [11]:
# metric_name = 'accuracy'
# batch_size = 16
# training_output_name = f'{pretrained_model_name}-finetuned-{actual_task}'

# benchmark_args = transformers.TrainingArguments(
#     training_output_name,
#     per_device_train_batch_size=16,
#     per_device_eval_batch_size=16,
#     num_train_epochs=3,
#     evaluation_strategy="epoch",
#     save_strategy="epoch",
#     load_best_model_at_end=True)

# benchmark_trainer = transformers.Trainer(
#     model_init = model_init,
#     args = benchmark_args,
#     train_dataset = train_dataset,
#     eval_dataset = eval_dataset,
#     tokenizer = tokenizer,
#     compute_metrics = compute_metrics
# )

In [12]:
# benchmark_trainer.train()

In [13]:
# benchmark_trainer.evaluate()

In [14]:
# benchmark_trainer.push_to_hub()

### Hyperparam search

Performing Hyper-param search to try to improve these metrics from benchmark :
1.  Validation Loss = 0.422 (reduce)
2.  Accuracy	= 0.842 (increase)




In [13]:
# Configure Trainer

metric_name = 'accuracy'
training_output_name = f'{pretrained_model_name}-finetuned-{actual_task}'
training_args = transformers.TrainingArguments(
    training_output_name,
    seed = random_seed,
    evaluation_strategy = "epoch",
    metric_for_best_model=metric_name)

hyperparam_trainer = transformers.Trainer(
    args=training_args,
    tokenizer=tokenizer,
    train_dataset=train_dataset, 
    eval_dataset=eval_dataset, 
    model_init=model_init,
    compute_metrics=compute_metrics)

/usr/local/lib/python3.8/dist-packages/torch/cuda/__init__.py:497: UserWarning: Can't initialize NVML
  warnings.warn("Can't initialize NVML")
loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--distilbert-base-uncased/snapshots/1c4513b2eedbda136f57676a34eea67aba266e5c/config.json
Model config DistilBertConfig {
  "_name_or_path": "distilbert-base-uncased",
  "activation": "gelu",
  "architectures": [
    "DistilBertForMaskedLM"
  ],
  "attention_dropout": 0.1,
  "dim": 768,
  "dropout": 0.1,
  "hidden_dim": 3072,
  "initializer_range": 0.02,
  "max_position_embeddings": 512,
  "model_type": "distilbert",
  "n_heads": 12,
  "n_layers": 6,
  "pad_token_id": 0,
  "qa_dropout": 0.1,
  "seq_classif_dropout": 0.2,
  "sinusoidal_pos_embds": false,
  "tie_weights_": true,
  "transformers_version": "4.25.1",
  "vocab_size": 30522
}

loading weights file pytorch_model.bin from cache at /root/.cache/huggingface/hub/models--distilbert-base-uncased/snapshots/1

In [18]:
tune_config = {
    'per_device_train_batch_size': 32,
    'per_device_eval_batch_size': 32,
    'num_train_epochs': tune.choice([2, 5]),
    'learning_rate' : tune.choice([0.0001, 0.0005, 0.00001, 0.00005]),
    'weight_decay' : tune.choice([0, 0.1, 0.01, 0.05, 0.001])}


# Start search
best_run = hyperparam_trainer.hyperparameter_search(hp_space=lambda _: tune_config, n_trials=10, direction='maximize')

No `resources_per_trial` arg was passed into `hyperparameter_search`. Setting it to a default value of 1 CPU for each trial.


== Status ==
Current time: 2023-01-23 15:02:45 (running for 00:00:01.70)
Memory usage on this node: 4.6/12.7 GiB 
Using FIFO scheduling algorithm.
Resources requested: 1.0/2 CPUs, 0/0 GPUs, 0.0/7.39 GiB heap, 0.0/3.69 GiB objects
Result logdir: /root/ray_results/_objective_2023-01-23_15-02-43
Number of trials: 10/10 (9 PENDING, 1 RUNNING)
+------------------------+----------+------------------+-----------------+--------------------+----------------+
| Trial name             | status   | loc              |   learning_rate |   num_train_epochs |   weight_decay |
|------------------------+----------+------------------+-----------------+--------------------+----------------|
| _objective_fd34d_00000 | RUNNING  | 172.28.0.12:8020 |          1e-05  |                  2 |          0.05  |
| _objective_fd34d_00001 | PENDING  |                  |          1e-05  |                  5 |          0.1   |
| _objective_fd34d_00002 | PENDING  |                  |          0.0001 |                  5 

(_objective pid=8020) Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_layer_norm.bias', 'vocab_projector.weight', 'vocab_projector.bias', 'vocab_layer_norm.weight', 'vocab_transform.weight', 'vocab_transform.bias']
(_objective pid=8020) - This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
(_objective pid=8020) - This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
(_objective pid=8020) Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-unc

== Status ==
Current time: 2023-01-23 15:02:51 (running for 00:00:07.90)
Memory usage on this node: 4.9/12.7 GiB 
Using FIFO scheduling algorithm.
Resources requested: 2.0/2 CPUs, 0/0 GPUs, 0.0/7.39 GiB heap, 0.0/3.69 GiB objects
Result logdir: /root/ray_results/_objective_2023-01-23_15-02-43
Number of trials: 10/10 (8 PENDING, 2 RUNNING)
+------------------------+----------+------------------+-----------------+--------------------+----------------+
| Trial name             | status   | loc              |   learning_rate |   num_train_epochs |   weight_decay |
|------------------------+----------+------------------+-----------------+--------------------+----------------|
| _objective_fd34d_00000 | RUNNING  | 172.28.0.12:8020 |          1e-05  |                  2 |          0.05  |
| _objective_fd34d_00001 | RUNNING  | 172.28.0.12:8112 |          1e-05  |                  5 |          0.1   |
| _objective_fd34d_00002 | PENDING  |                  |          0.0001 |                  5 

(_objective pid=8112) Some weights of the model checkpoint at distilbert-base-uncased were not used when initializing DistilBertForSequenceClassification: ['vocab_transform.weight', 'vocab_projector.bias', 'vocab_layer_norm.bias', 'vocab_transform.bias', 'vocab_projector.weight', 'vocab_layer_norm.weight']
(_objective pid=8112) - This IS expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
(_objective pid=8112) - This IS NOT expected if you are initializing DistilBertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
(_objective pid=8112) Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at distilbert-base-unc

...

== Status ==
Current time: 2023-01-23 17:33:08 (running for 02:30:24.60)
Memory usage on this node: 6.0/12.7 GiB 
Using FIFO scheduling algorithm.
Resources requested: 1.0/2 CPUs, 0/0 GPUs, 0.0/7.39 GiB heap, 0.0/3.69 GiB objects
Result logdir: /root/ray_results/_objective_2023-01-23_15-02-43
Number of trials: 10/10 (1 RUNNING, 9 TERMINATED)
+------------------------+------------+------------------+-----------------+--------------------+----------------+-------------+
| Trial name             | status     | loc              |   learning_rate |   num_train_epochs |   weight_decay |   objective |
|------------------------+------------+------------------+-----------------+--------------------+----------------+-------------|
| _objective_fd34d_00008 | RUNNING    | 172.28.0.12:8020 |          0.0001 |                  5 |          0.001 |    0.851765 |
| _objective_fd34d_00000 | TERMINATED | 172.28.0.12:8020 |          1e-05  |                  2 |          0.05  |    0.545882 |
| _objectiv

(_objective pid=8020) 
 93%|█████████▎| 25/27 [00:56<00:04,  2.41s/it]
(_objective pid=8020) 
 96%|█████████▋| 26/27 [00:58<00:02,  2.31s/it]


== Status ==
Current time: 2023-01-23 17:33:13 (running for 02:30:29.60)
Memory usage on this node: 6.0/12.7 GiB 
Using FIFO scheduling algorithm.
Resources requested: 1.0/2 CPUs, 0/0 GPUs, 0.0/7.39 GiB heap, 0.0/3.69 GiB objects
Result logdir: /root/ray_results/_objective_2023-01-23_15-02-43
Number of trials: 10/10 (1 RUNNING, 9 TERMINATED)
+------------------------+------------+------------------+-----------------+--------------------+----------------+-------------+
| Trial name             | status     | loc              |   learning_rate |   num_train_epochs |   weight_decay |   objective |
|------------------------+------------+------------------+-----------------+--------------------+----------------+-------------|
| _objective_fd34d_00008 | RUNNING    | 172.28.0.12:8020 |          0.0001 |                  5 |          0.001 |    0.858824 |
| _objective_fd34d_00000 | TERMINATED | 172.28.0.12:8020 |          1e-05  |                  2 |          0.05  |    0.545882 |
| _objectiv

(_objective pid=8020) 
100%|██████████| 27/27 [01:00<00:00,  2.00s/it]
                                                 
100%|██████████| 135/135 [26:43<00:00, 11.88s/it]
2023-01-23 17:33:13,532	INFO tune.py:762 -- Total run time: 9029.82 seconds (9029.64 seconds for the tuning loop).


== Status ==
Current time: 2023-01-23 17:33:13 (running for 02:30:29.68)
Memory usage on this node: 5.9/12.7 GiB 
Using FIFO scheduling algorithm.
Resources requested: 0/2 CPUs, 0/0 GPUs, 0.0/7.39 GiB heap, 0.0/3.69 GiB objects
Result logdir: /root/ray_results/_objective_2023-01-23_15-02-43
Number of trials: 10/10 (10 TERMINATED)
+------------------------+------------+------------------+-----------------+--------------------+----------------+-------------+
| Trial name             | status     | loc              |   learning_rate |   num_train_epochs |   weight_decay |   objective |
|------------------------+------------+------------------+-----------------+--------------------+----------------+-------------|
| _objective_fd34d_00000 | TERMINATED | 172.28.0.12:8020 |          1e-05  |                  2 |          0.05  |    0.545882 |
| _objective_fd34d_00001 | TERMINATED | 172.28.0.12:8112 |          1e-05  |                  5 |          0.1   |    0.84     |
| _objective_fd34d_0000

In [19]:
# Peek at best run
best_run

BestRun(run_id='fd34d_00004', objective=0.8623529411764705, hyperparameters={'per_device_train_batch_size': 32, 'per_device_eval_batch_size': 32, 'num_train_epochs': 5, 'learning_rate': 5e-05, 'weight_decay': 0.001})

In [23]:
# Set optimized-params from best_run
for n, v in best_run.hyperparameters.items():
    setattr(hyperparam_trainer.args, n, v)

# run training again
hyperparam_trainer.train()

loading configuration file config.json from cache at /root/.cache/huggingface/hub/models--distilbert-base-uncased/snapshots/1c4513b2eedbda136f57676a34eea67aba266e5c/config.json
Model config DistilBertConfig {
  "_name_or_path": "distilbert-base-uncased",
  "activation": "gelu",
  "architectures": [
    "DistilBertForMaskedLM"
  ],
  "attention_dropout": 0.1,
  "dim": 768,
  "dropout": 0.1,
  "hidden_dim": 3072,
  "initializer_range": 0.02,
  "max_position_embeddings": 512,
  "model_type": "distilbert",
  "n_heads": 12,
  "n_layers": 6,
  "pad_token_id": 0,
  "qa_dropout": 0.1,
  "seq_classif_dropout": 0.2,
  "sinusoidal_pos_embds": false,
  "tie_weights_": true,
  "transformers_version": "4.25.1",
  "vocab_size": 30522
}

loading weights file pytorch_model.bin from cache at /root/.cache/huggingface/hub/models--distilbert-base-uncased/snapshots/1c4513b2eedbda136f57676a34eea67aba266e5c/pytorch_model.bin
Some weights of the model checkpoint at distilbert-base-uncased were not used when in

The following columns in the evaluation set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: sentence, idx. If sentence, idx are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 850
  Batch size = 32
The following columns in the evaluation set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: sentence, idx. If sentence, idx are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this message.
***** Running Evaluation *****
  Num examples = 850
  Batch size = 32
The following columns in the evaluation set don't have a corresponding argument in `DistilBertForSequenceClassification.forward` and have been ignored: sentence, idx. If sentence, idx are not expected by `DistilBertForSequenceClassification.forward`,  you can safely ignore this messa

TrainOutput(global_step=135, training_loss=0.2166046142578125, metrics={'train_runtime': 1287.5335, 'train_samples_per_second': 3.301, 'train_steps_per_second': 0.105, 'total_flos': 44342426798544.0, 'train_loss': 0.2166046142578125, 'epoch': 5.0})

In [21]:
# Peek at the optimized-params
best_run.hyperparameters.items()

dict_items([('per_device_train_batch_size', 32), ('per_device_eval_batch_size', 32), ('num_train_epochs', 5), ('learning_rate', 5e-05), ('weight_decay', 0.001)])

In [26]:
# Peek at evaluation params
print('per_device_train_batch_size :', hyperparam_trainer.args.per_device_train_batch_size)
print('num_train_epochs :', hyperparam_trainer.args.num_train_epochs)
print('learning_rate :', hyperparam_trainer.args.learning_rate)
print('weight_decay :', hyperparam_trainer.args.weight_decay)

per_device_train_batch_size : 32
num_train_epochs : 5
learning_rate : 5e-05
weight_decay : 0.001


In [27]:
hyperparam_trainer.push_to_hub(commit_message='Performed Hyperparameter search')

Cloning https://huggingface.co/naksu/distilbert-base-uncased-finetuned-sst2 into local empty directory.


Download file pytorch_model.bin:   0%|          | 8.00k/255M [00:00<?, ?B/s]

Download file training_args.bin: 100%|##########| 3.37k/3.37k [00:00<?, ?B/s]

Download file runs/Jan23_06-33-38_1ef5a0f51472/events.out.tfevents.1674455640.1ef5a0f51472.315.8: 100%|#######…

Download file runs/Jan23_06-39-15_1ef5a0f51472/1674455962.2194076/events.out.tfevents.1674455962.1ef5a0f51472.…

...

Saving model checkpoint to distilbert-base-uncased-finetuned-sst2
Configuration saved in distilbert-base-uncased-finetuned-sst2/config.json
Model weights saved in distilbert-base-uncased-finetuned-sst2/pytorch_model.bin
tokenizer config file saved in distilbert-base-uncased-finetuned-sst2/tokenizer_config.json
Special tokens file saved in distilbert-base-uncased-finetuned-sst2/special_tokens_map.json


Upload file pytorch_model.bin:   0%|          | 32.0k/255M [00:00<?, ?B/s]

Upload file training_args.bin: 100%|##########| 3.37k/3.37k [00:00<?, ?B/s]

remote: Scanning LFS files for validity, may be slow...        
remote: LFS file scan complete.        
To https://huggingface.co/naksu/distilbert-base-uncased-finetuned-sst2
   4ce09cd..5cd199f  main -> main

remote: LFS file scan complete.        
To https://huggingface.co/naksu/distilbert-base-uncased-finetuned-sst2
   4ce09cd..5cd199f  main -> main

To https://huggingface.co/naksu/distilbert-base-uncased-finetuned-sst2
   5cd199f..684437d  main -> main

   5cd199f..684437d  main -> main



'https://huggingface.co/naksu/distilbert-base-uncased-finetuned-sst2/commit/5cd199f442d504d7e770e8d518191fa5b1013339'